In [1]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [2]:
model_type = "molemb"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev4"
args.n_epochs = 10000 
args.init_model = "{}-attention-sink6-test8".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = False 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 1001
args.conn_lambda_epochs_end = 3000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 1001
args.valency_lambda_epochs_end = 3000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 1001
args.euler_lambda_epochs_end = 3000
args.tau_start = 1
args.tau_end = 0.01
args.tau_epochs_start = 1
args.tau_epochs_end = 4000

args.cross_att_use = True
args.cross_att_random = False
args.cross_att_n_sinkhorn = 6
# args.morgan_bits = 1024

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=3000, conn_lambda_epochs_start=1001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=6, cross_att_random=False, cross_att_use=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=3000, euler_lambda_epochs_start=1001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', init_decoder_model='molemb-attention-sink6-test8_decode', init_model='molemb-attention-sink6-test8', linear_out=False, max_num_atoms=70, model_type='molemb', morgan_bits=0, n_epochs=10000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, one_batch_train=False, ot_solver='emd', output_dir='mol_opt/output_dev4/molemb

In [3]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [5]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

Found previous model mol_opt/output_dev4/molemb-attention-sink6-test8/model_molemb-attention-sink6-test8_120, epoch 120. Overwriting args.
Penalty params: tau=0.87194 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=120 mode=[0 0 0] conn=True val=True euler=True
Epoch: 121


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:12.4444458
 conn_penalty:0.0000000
 val_penalty:0.3023366
 euler_penalty:5.1422925
 total:12.4498706
Penalty params: tau=0.87093 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=121 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.87093 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=121 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 121, train
 fgw:12.4444458
 conn_penalty:0.0000000
 val_penalty:0.3023366
 euler_penalty:5.1422925
 total:12.4498706
Epoch duration: 3.9701859951019287
Epoch: 122
Losses Batch 0, train
 fgw:12.4477393
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:12.4477393
Penalty params: tau=0.86993 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=122 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.86993 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=122 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 122, train
 fgw:12.4477393
 conn_penalt

Losses Batch 0, train
 fgw:12.4372400
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:12.4372400
Penalty params: tau=0.85602 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=136 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.85602 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=136 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 136, train
 fgw:12.4372400
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:12.4372400
Epoch duration: 0.8618521690368652
Epoch: 137
Losses Batch 0, train
 fgw:12.4365540
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:12.4365540
Penalty params: tau=0.85503 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=137 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.85503 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=137 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 137, train
 fgw:12.4365540
 conn_penalt

Losses Batch 0, train
 fgw:12.4323035
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:12.4323035
Penalty params: tau=0.84136 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=151 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.84136 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=151 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 151, train
 fgw:12.4323035
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:12.4323035
Epoch duration: 0.8559911251068115
Epoch: 152
Losses Batch 0, train
 fgw:12.4319958
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:12.4319958
Penalty params: tau=0.84039 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=152 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.84039 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=152 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 152, train
 fgw:12.4319958
 conn_penalt

...

Losses Batch 0, train
 fgw:848.0475781
 conn_penalty:33.9017188
 val_penalty:24.3000000
 euler_penalty:8.5600000
 total:1088.3727344
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8848 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8848 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8848, train
 fgw:848.0475781
 conn_penalty:33.9017188
 val_penalty:24.3000000
 euler_penalty:8.5600000
 total:1088.3727344
Epoch duration: 3.666473627090454
Epoch: 8849
Losses Batch 0, train
 fgw:828.5305469
 conn_penalty:43.5174609
 val_penalty:22.4800000
 euler_penalty:7.2000000
 total:1085.8829687
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8849 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8849 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8849, train
 fgw:828.5305469
 c

Losses Batch 0, train
 fgw:702.4185938
 conn_penalty:130.4688672
 val_penalty:18.0200000
 euler_penalty:15.0200000
 total:1213.9651563
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8863 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8863 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8863, train
 fgw:702.4185938
 conn_penalty:130.4688672
 val_penalty:18.0200000
 euler_penalty:15.0200000
 total:1213.9651563
Epoch duration: 3.7168447971343994
Epoch: 8864
Losses Batch 0, train
 fgw:695.5295312
 conn_penalty:132.0615039
 val_penalty:18.1600000
 euler_penalty:15.3000000
 total:1213.1140625
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8864 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8864 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8864, train
 fgw:695.529

Losses Batch 0, train
 fgw:1197.3566406
 conn_penalty:3.7410034
 val_penalty:44.5800000
 euler_penalty:27.7400000
 total:1486.9596875
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8878 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8878 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8878, train
 fgw:1197.3566406
 conn_penalty:3.7410034
 val_penalty:44.5800000
 euler_penalty:27.7400000
 total:1486.9596875
Epoch duration: 3.646009922027588
Epoch: 8879
Losses Batch 0, train
 fgw:1198.3760938
 conn_penalty:3.6277130
 val_penalty:43.1400000
 euler_penalty:26.3400000
 total:1477.6392188
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8879 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8879 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8879, train
 fgw:1198.376093

Losses Batch 0, train
 fgw:896.9364063
 conn_penalty:26.8797241
 val_penalty:23.9000000
 euler_penalty:4.3400000
 total:1105.7555469
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8893 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8893 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8893, train
 fgw:896.9364063
 conn_penalty:26.8797241
 val_penalty:23.9000000
 euler_penalty:4.3400000
 total:1105.7555469
Epoch duration: 3.135230302810669
Epoch: 8894
Losses Batch 0, train
 fgw:875.4537500
 conn_penalty:29.3447803
 val_penalty:23.3200000
 euler_penalty:3.7200000
 total:1087.5281250
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8894 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=8894 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 8894, train
 fgw:875.4537500
 c

KeyboardInterrupt: 